In [4]:
import google.generativeai as genai
import utils
import os
from getpass import getpass
import json

In [ ]:
os.environ['GEMINI_API_KEY'] = getpass("Your gemini API key: ")

def configure():
    sqldb = utils.ArxivSQL()
    db = utils.ArxivChroma()
    gemini_api_key = os.getenv("GEMINI_API_KEY")
    if not gemini_api_key:
        raise ValueError(
            "Gemini API Key not provided. Please provide GEMINI_API_KEY as an environment variable"
        )
    genai.configure(api_key=gemini_api_key)
    model = genai.GenerativeModel("gemini-pro")
    return model, sqldb, db


model, sqldb, db = configure()

In [2]:
def extract_keyword_prompt(query):
    """A prompt that return a JSON block as arguments for querying database"""

    prompt = (
        """[INST] You are an assistant that choose only one action below based on guest question.
   1. If the guest question is asking for some specific document or article, you need to respond the information in JSON format with 2 keys "title", "author" if found any above. The authors are separated with the word 'and'. 
   2. If the guest question is asking for relevant informations about a topic, you need to respond the information in JSON format with 2 keys "keywords", "description", include a list of keywords represent the main academic topic, \
     and a description about the main topic. You may paraphrase the keywords to add more. \
   3. If the guest is not asking for any informations or documents, you need to respond with a polite answer in JSON format with 1 key "answer".
   QUESTION: '{query}'
   [/INST]
   ANSWER: 
   """
    ).format(query=query)

    return prompt

def make_answer_prompt(input, contexts):
    """A prompt that return the final answer, based on the queried context"""

    prompt = (
        """[INST] You are an library assistant that help to search articles and documents based on user's question.
  From guest's question, you have found some records and documents that may help. Now you need to answer the guest with the information found.
  You should answer in a conversational form politely.
  QUESTION: '{input}'
  INFORMATION: '{contexts}'
  [/INST]
  ANSWER:
  """
    ).format(input=input, contexts=contexts)

    return prompt

In [3]:
def response(args):
    """Create response context, based on input arguments"""
    keys = list(dict.keys(args))
    if "answer" in keys:
        return args['answer'], None  # trả lời trực tiếp
    
    if "keywords" in keys:
        # perform query
        query_texts = args["description"]
        keywords = args["keywords"]
        results = db.query_relevant(keywords=keywords, query_texts=query_texts)
        # print(results)
        ids = results['metadatas'][0]
        paper_id = [id['paper_id'] for id in ids]
        paper_info = sqldb.query_id(paper_id)
        # print(paper_info)
        records = [] # get title (2), author (3), link (6)
        result_string = ""
        for i in range(len(paper_id)):
            result_string += "Title: {}, Author: {}, Link: {}".format(paper_info[i][2],paper_info[i][3],paper_info[i][6])
            records.append([paper_info[i][2],paper_info[i][3],paper_info[i][6]])
        # process results:
        return result_string, records
        # invoke llm and return result

    if "title" in keys:
        results = sqldb.query(title = args['title'],author = args['author'])
        print(results)
        paper_info = sqldb.query(title = args['title'],author = args['author'])
        # if query not found then go crawl brh

        if len(paper_info) == 0:
            new_records = utils.crawl_exact_paper(title=args['title'],author=args['author'])
            db.add(new_records)
            sqldb.add(new_records)
            paper_info = sqldb.query(title = args['title'],author = args['author'])
        # -------------------------------------
        records = [] # get title (2), author (3), link (6)
        result_string = ""
        for i in range(len(paper_info)):
            result_string += "Title: {}, Author: {}, Link: {}".format(paper_info[i][2],paper_info[i][3],paper_info[i][6])
            records.append([paper_info[i][2],paper_info[i][3],paper_info[i][6]])
        # process results:
        if len(result_string) == 0:
            return "Information not found", None
        return result_string, records
        # invoke llm and return result

In [8]:
import json
# test first step
# input_prompt = input()
input_prompt = "I'm working on a LSTM model to recognize actions in a video, recommend me some related papers"
first_prompt = extract_keyword_prompt(input_prompt)
# print(first_prompt)
# answer = model.invoke(first_prompt,
#                       temperature=0.0) # ctrans
answer = model.generate_content(first_prompt).text
print("--------------------------")
print(answer)
args = json.loads(utils.trimming(answer))
# print(args)
response(args)

--------------------------
{
 "keywords": ["Video action recognition", "Long Short-Term Memory", "Computer vision", "Deep learning", "Time series analysis"],
 "description": "Video action recognition is a challenging task in computer vision. It requires the ability to understand the temporal dynamics of a video and to identify the actions being performed. Long Short-Term Memory (LSTM) networks are a type of recurrent neural network that is well-suited for learning long-term dependencies. This makes them a good choice for video action recognition tasks. LSTM networks have been shown to achieve state-of-the-art results on a variety of video action recognition datasets using deep learning techniques."
}


('Title: Applications of Deep Neural Networks with Keras, Author: Jeff Heato, Link: http://arxiv.org/pdf/2009.05673v5Title: DeepDrum: An Adaptive Conditional Neural Network, Author: Dimos Makris, Maximos Kaliakatsos-Papakostas, Katia Lida Kermanidi, Link: http://arxiv.org/pdf/1809.06127v2Title: A Video Recognition Method by using Adaptive Structural Learning of Long Short Term Memory based Deep Belief Network, Author: Shin Kamada, Takumi Ichimur, Link: http://arxiv.org/pdf/1909.13480v1',
 [['Applications of Deep Neural Networks with Keras',
   'Jeff Heato',
   'http://arxiv.org/pdf/2009.05673v5'],
  ['DeepDrum: An Adaptive Conditional Neural Network',
   'Dimos Makris, Maximos Kaliakatsos-Papakostas, Katia Lida Kermanidi',
   'http://arxiv.org/pdf/1809.06127v2'],
  ['A Video Recognition Method by using Adaptive Structural Learning of Long Short Term Memory based Deep Belief Network',
   'Shin Kamada, Takumi Ichimur',
   'http://arxiv.org/pdf/1909.13480v1']])

In [10]:
# test response, second step
input_prompt = "I'm working on a LSTM model to recognize actions in a video, recommend me some related papers"
args =  {
      "keywords": ["LSTM model", "video analysis", "action recognition"],
      "description": "For recognizing actions in videos using Long Short-Term Memory (LSTM) models, you may find the following papers insightful. These studies explore various aspects of action recognition using LSTM: (1) 'Action Recognition with 3D Convolutional Neural Networks and Long Short-Term Memory' by Tran et al., 2015; (2) 'ConvLSTM: A Convolutional Neural Network for Video Recognition' by Shi et al., 2015; (3) 'Using Long-Short Term Memory for Action Recognition in Videos' by Graves, 2013."
    }
contexts, results = response(args)
if not results:
  # direct answer
    print(contexts)
else:
  output_prompt = make_answer_prompt(input_prompt,contexts)
  # answer = model.invoke(output_prompt,
  #                       temperature=0.3) # ctrans
  answer = model(prompt=output_prompt,
               temperature=0.0,
               max_tokens=1024,
               ) # llama
  print("------------------------")
  print(answer['choices'][0]['text'])

For recognizing actions in videos using Long Short-Term Memory (LSTM) models, you may find the following papers insightful. These studies explore various aspects of action recognition using LSTM: (1) 'Action Recognition with 3D Convolutional Neural Networks and Long Short-Term Memory' by Tran et al., 2015; (2) 'ConvLSTM: A Convolutional Neural Network for Video Recognition' by Shi et al., 2015; (3) 'Using Long-Short Term Memory for Action Recognition in Videos' by Graves, 2013.
['LSTM model', 'video analysis', 'action recognition']


Llama.generate: prefix-match hit

llama_print_timings:        load time =  139768.70 ms
llama_print_timings:      sample time =     140.16 ms /   412 runs   (    0.34 ms per token,  2939.41 tokens per second)
llama_print_timings: prompt eval time =       0.00 ms /     1 tokens (    0.00 ms per token,      inf tokens per second)
llama_print_timings:        eval time =   91570.34 ms /   412 runs   (  222.26 ms per token,     4.50 tokens per second)
llama_print_timings:       total time =   93048.98 ms /   413 tokens


------------------------
Hello there! I see that you're working on an LSTM model for recognizing actions in videos. I have found some related papers that might be of interest to you.

  1. The first one is titled "Action in Mind: A Neural Network Approach to Action Recognition and Segmentation" by Zahra Gharae. This paper proposes a neural network approach for action recognition and segmentation, which could provide some insights into your work with LSTM models. You can find it at this link: <http://arxiv.org/pdf/2104.14870v1>

  2. Another interesting paper is "Deep Neural Networks in Video Human Action Recognition: A Review" by Zihan Wang, Yang Yang, Zhi Liu, and Yifan Zhen. This review discusses the application of deep neural networks for video human action recognition. It could give you a broader perspective on the current state-of-the-art methods in this field. You can access it here: <http://arxiv.org/pdf/2305.15692v1>

  3. Lastly, there's "3D Convolutional Neural Networks for U

In [5]:
# full chain
# inference time depends on hardware ability :')
# with CPU i7-8750H, 16GB RAM and no GPU cuda, expect inference time up to 5-6 min
# input_prompt = input()
input_prompt = "I'm working on a LSTM model to recognize actions in a video, recommend me some related papers"
first_prompt = extract_keyword_prompt(input_prompt)
# print(first_prompt)
# answer = model.invoke(first_prompt,
#                       temperature=0.0) # ctrans
answer = model.generate_content(first_prompt).text
print("--------------------------")
print(answer)
args = json.loads(utils.trimming(answer))
# print(args)
contexts, results = response(args)
if not results:
  # direct answer
    print(contexts)
else:
  output_prompt = make_answer_prompt(input_prompt,contexts)
  # answer = model.invoke(output_prompt,
  #                       temperature=0.3) # ctrans, answer is a string
  answer = model.generate_content(output_prompt).text # llama, answer is a dict
  print("--------------------------")
  print(answer)

--------------------------
```json
{
  "keywords": [
    "Video Recognition",
    "LSTM",
    "Action Recognition",
    "Deep Learning"
  ],
  "description": "Action recognition in videos is a challenging task due to the large variations in appearance, scale, and viewpoint. LSTM models have been shown to be effective for this task, as they can learn long-term dependencies in the data. Some related papers that you may find useful include:\n\n1. [Long-term recurrent convolutional networks for visual recognition](https://arxiv.org/abs/1411.4389) by Karen Simonyan and Andrew Zisserman\n2. [Two-stream convolutional networks for action recognition in videos](https://arxiv.org/abs/1406.2199) by Karen Simonyan and Andrew Zisserman\n3. [LSTM networks for video action recognition](https://arxiv.org/abs/1502.04793) by Jeff Donahue, Lisa Anne Hendricks, Sergio Guadarrama, Marcus Rohrbach, Subhashini Venugopalan, Kate Saenko, and Trevor Darrell"
}
```
--------------------------
Of course, here are 

In [17]:
!pip freeze > requirements.txt